In [143]:

from typing import Callable, Tuple, TypeVar, cast, get_origin, get_args, Union, Any, Optional, Dict, List
from components.two_wheels import TwoWheelsV3
from components import (
    CallChannel, 
    ComponentStarter, 
    LoggerComponent,
    BlueToothCarControlSPP_V2,
    start_bluetooth_server_v2b, 
    AngularSpeedControlV3,
    Picamera2V2,
    PitchAngularVelocityController, 
    get_switches,
    MicrophoneComponent
)

from data_collection.data_collection import LoggerSet
from multiprocessing import Manager
import numpy as np
import datetime
import RPi.GPIO as GPIO
GPIO.setmode(GPIO.BOARD)

# from components import numpy_sample_setup
# r, w = numpy_sample_setup(['d', 'd'], [0, 0])

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [144]:
name = 'ee_plus_noise_closer'

loggerset = LoggerSet(f'../log/audio_{name}'+str(datetime.datetime.now()), overwrite_ok=False)
manager = Manager()

In [145]:

logger_process = ComponentStarter(
    LoggerComponent, 
    manager, 
    init_kwargs=dict(
        loggerset = loggerset
    )
)

mic_com = ComponentStarter(
    MicrophoneComponent, 
    manager, 
    instantiator=MicrophoneComponent.entry, 
    init_kwargs = dict(
        device_indices=[9, 10]
    )
)


In [146]:

two_wheel_process = ComponentStarter(
    TwoWheelsV3, 
    manager, 
    init_kwargs=dict(
        left_pin = 33, 
        right_pin = 32, 
        dir_pins = (16, 18), 
        name='TwoWheelsV3'
    ),
    loop_intervals={'step': 1/100},
    instantiator = TwoWheelsV3.entry

)

angular_speed_control_process = ComponentStarter(
    AngularSpeedControlV3, 
    manager, 
    init_kwargs=dict(
        i2c_address=0x68, 
        bus_num=1,
        name='AngularSpeedControlV3'
    ),
    loop_intervals={'step': 1/100},
    instantiator = AngularSpeedControlV3.entry
)

bluetooth_control_process = ComponentStarter(
    BlueToothCarControlSPP_V2, 
    manager, 
    init_kwargs={},
    loop_intervals={'step': 1/100},
)

bt_ser_out, bt_ser_process_man = start_bluetooth_server_v2b(manager)


In [147]:
mic_com.register_outgoing_rpc(
    dict(log=logger_process.incoming_rpcs['log'])

)

In [148]:
two_wheel_process.register_outgoing_rpc(
    dict(log=logger_process.incoming_rpcs['log'])
)

angular_speed_control_process.register_outgoing_rpc(
    dict(log=logger_process.incoming_rpcs['log'])
)

bluetooth_control_process.register_outgoing_rpc(
    dict(log=logger_process.incoming_rpcs['log'])
)


two_wheel_process.register_incoming_samples(
    angular_speed_control_process.outgoing_sample_readers
)

angular_speed_control_process.register_incoming_samples(
    bluetooth_control_process.outgoing_samples
)

bluetooth_control_process.register_incoming_samples(
    bt_ser_out
)


In [149]:
logger_process.start()
mic_com.start()

saving: BlueToothCarControlSPP_V2
saving: TwoWheelsV3
saving: AngularSpeedControlV3
saving: MicrophoneComponent
saving: BlueToothCarControlSPP_V2
saving: TwoWheelsV3
saving: AngularSpeedControlV3
saving: MicrophoneComponent
saving: BlueToothCarControlSPP_V2
saving: TwoWheelsV3
saving: AngularSpeedControlV3
saving: MicrophoneComponent
saving: TwoWheelsV3
saving: BlueToothCarControlSPP_V2
saving: AngularSpeedControlV3
saving: MicrophoneComponent


In [150]:
bt_ser_process_man.start()
bluetooth_control_process.start()
two_wheel_process.start()
angular_speed_control_process.start()


Making discoverable...
Starting Serial Port Profile...


/home/kawa/projects/car1/src/components/syncronisation/__init__.py:224: UserWarning: the real interval is >= ideal_interval
  warnings.warn("the real interval is >= ideal_interval")
/home/kawa/projects/car1/src/components/two_wheels.py:17: RuntimeWarning: This channel is already in use, continuing anyway.  Use GPIO.setwarnings(False) to disable warnings.
  GPIO.setup(pin, GPIO.OUT) #type: ignore
/home/kawa/projects/car1/src/components/two_wheels.py:73: RuntimeWarning: This channel is already in use, continuing anyway.  Use GPIO.setwarnings(False) to disable warnings.
  GPIO.setup(dir_pins[0], GPIO.OUT) #type: ignore
/home/kawa/projects/car1/src/components/two_wheels.py:74: RuntimeWarning: This channel is already in use, continuing anyway.  Use GPIO.setwarnings(False) to disable warnings.
  GPIO.setup(dir_pins[1], GPIO.OUT) #type: ignore
/home/kawa/projects/car1/src/components/syncronisation/__init__.py:224: UserWarning: the real interval is >= ideal_interval
  warnings.warn("the real i

NewConnection(/org/bluez/hci0/dev_C8_BD_4D_BA_4F_15, 115)


In [151]:
bt_ser_process_man.terminate()
bluetooth_control_process.process_starter.terminate()
#logger_process.process_starter.terminate()
two_wheel_process.process_starter.terminate()
angular_speed_control_process.process_starter.terminate()



In [152]:
logger_process.incoming_rpcs['save_logger'].call('TwoWheelsV3')
logger_process.incoming_rpcs['save_logger'].call('BlueToothCarControlSPP_V2')
logger_process.incoming_rpcs['save_logger'].call('AngularSpeedControlV3')



<function components.syncronisation.CallChannel.call.<locals>.await_result(timeout: Optional[float] = None)>

In [153]:
mic_com.process_starter.terminate()
logger_process.incoming_rpcs['save_logger'].call('MicrophoneComponent')

log = logger_process.incoming_rpcs['get_logger'].call('MicrophoneComponent')()
_, l = log
df = l.load_as_df()

/home/kawa/projects/car1/src/data_collection/data_collection.py:110: UserWarning: log is not availble after depickling/__setstate__
  warnings.warn('log is not availble after depickling/__setstate__')


/home/kawa/projects/car1/src/data_collection/data_collection.py:110: UserWarning: log is not availble after depickling/__setstate__
  warnings.warn('log is not availble after depickling/__setstate__')


# get data

In [154]:
import numpy as np
import datetime
from data_collection.data_collection import Logger
import plotly.express as px
from IPython.display import Audio


In [116]:

# sesspath = '../log/audio_running_noise2024-08-04 07:54:31.987854'
# l = Logger(sesspath,name='MicrophoneComponent', overwrite_ok=True)
# df = l.load_as_df()

In [155]:
t = df['audio'].apply(lambda x: [np.concatenate(x[i]) for i in x])
t = t.tolist()
c0a = np.concatenate([t_[0] for t_ in t])
c1a = np.concatenate([t_[1] for t_ in t])


In [156]:
Audio(c1a.flatten(), rate=16000)

In [141]:
Audio(c0a.flatten(), rate=16000)

In [142]:
from scipy.io.wavfile import write
write(f'{name}_c0.wav', 16000, c0a.flatten())
write(f'{name}_c1.wav', 16000, c1a.flatten())
